In [ ]:
%load_ext autoreload
%autoreload 2

# Semantic Knowledge

This will process the transcripts/annotations (which would be considered autobiographical knowledge) to extract the meaning of the emotion words, i.e. semantic knowledge, as subclass of an nltk naive Bayes classifier
- the features/observations/data are a set of (question, answer) pairs
- the models/hypotheses are the emotion words
- the data gives us P(observation|emotion word)
- the task goal is to calculate P(emotion word|observation)
- the prior P(emotion word) = 1/(# of emotion words), i.e. a uniform, non-informative prior

In [ ]:
from emo20q.semanticknowledge import SemanticKnowledge
k = SemanticKnowledge()

In [ ]:
print(k.entities())

{'maudlin', 'being appalled', 'mischievous', 'grumpiness', 'mad', 'disgust', 'content', 'enthusiasm', 'cheerfulness', 'tense', 'patience', 'fear', 'despise', 'maniacal', 'delirium', 'loved', 'lust', 'downcast', 'sympathy', 'inquisitiveness', 'irritated', 'silly', 'angry', 'proud', 'love', 'stupor', 'jubilance', 'pessimism', 'concern', 'devastation', 'pride', 'hunger', 'curiosity', 'determination', 'wariness', 'anger', 'annoyed', 'energetic', 'apathy', 'envy', 'excitement', 'remorse', 'uninterested', 'surprise', 'enamored', 'amusement', 'jilted', 'glee', 'guilt', 'sarcasm', 'aversion', 'quixotic', 'caring', 'empathy', 'relaxation', 'admiration', 'unsure', 'hate', 'respect', 'anxiety', 'joyfulness', 'shame', 'hope', 'shyness', 'thrill', 'hopelessness', 'conflicted', 'pleasure', 'disillusionment', 'feelingLucky', 'scared', 'boredom', 'melancholy', 'joy', 'dumbfounded', 'nervousness', 'tiredness', 'contentment', 'suspicion', 'educated', 'insecurity', 'inspiration', 'irritation', 'thankfuln

In [ ]:
print(k.most_informative_features(20))

[('e.valence==positive', 'no'), ('e==happiness', 'no'), ('e.valence==negative', 'yes'), ('associated(e,happiness)', 'no'), ('e.activation==high', 'no'), ('e.activation==high', 'other'), ('cause(e,feelGood)', 'other'), ('e.valence==negative', 'no'), ('e.duration==long', 'no'), ('e.valence==positive', 'other'), ('e==happiness', 'yes'), ('e==depression', 'yes'), ('cause(something,e)', 'no'), ('directed(e,otherPerson)', 'yes'), ('directed(e,otherPerson)', 'other'), ('directed(e,otherPerson)', 'no'), ('e.duration==long', 'other'), ('similar(e,happiness)', 'other'), ('cause(something,e)', 'other'), ('e==hope', 'yes')]


## semantic knowledge is subclassed from nltk.classify.naivebayes
https://www.nltk.org/_modules/nltk/classify/naivebayes.html
which in turn is a subclass of the classifier interface:
https://www.nltk.org/api/nltk.classify.html
Also used is FreqDist and ELEProbDist (.5 smoothing) from nltk.probability
- I think that the ELEProbDist is not used 
- in gpdaquestioner, UniformProbDist is used

In [ ]:
print("observed label/emotion frequencies:")
print(k._label_freqdist)
for lab in k._label_freqdist:
 print(lab, k._label_freqdist[lab])

observed label/emotion frequencies:
<FreqDist with 167 samples and 593 outcomes>
happiness 61
anger 40
sadness 33
love 27
frustration 21
confusion 18
depression 17
jealousy 13
excitement 13
fear 12
euphoria 10
surprise 8
disgust 8
anxiety 8
envy 8
hope 8
nervousness 8
concern 8
elation 7
melancholy 6
regret 6
tiredness 6
boredom 5
relief 5
contentment 5
hatred 5
thrill 4
worry 4
embarrassment 4
guilt 4
loneliness 4
joy 4
fury 4
disappointment 4
relaxation 4
nostalgia 4
calm 3
shame 3
enthusiasm 3
mad 3
pity 3
annoyance 3
pride 3
cheerfulness 3
apathy 3
resentment 3
obsession 3
remorse 3
proud 2
serenity 2
thankfulness 2
bravery 2
gratefulness 2
scared 2
distress 2
affection 2
suffering 2
eagerness 2
shyness 2
misery 2
satisfaction 2
sorrow 2
exhaustion 2
stress 2
dissatisfied 2
lust 2
hostility 2
agitation 2
quixotic 2
conflicted 2
perplexity 2
ambivalence 2
inquisitiveness 2
discontentment 2
angry 2
astounded 2
overwhelmed 2
accepting 2
disillusionment 2
hate 2
silly 1
adoration 1
adm

In [ ]:
print("observed label/emotion probabilities:")
print(k._label_probdist)
for lab in k._label_freqdist:
 print(lab, k._label_probdist.prob(lab))

observed label/emotion probabilities:
<ELEProbDist based on 593 samples>
happiness 0.09090909090909091
anger 0.0598669623059867
sadness 0.04951958610495196
love 0.04065040650406504
frustration 0.031781226903178125
confusion 0.027346637102734665
depression 0.025868440502586843
jealousy 0.019955654101995565
excitement 0.019955654101995565
fear 0.018477457501847747
euphoria 0.015521064301552107
surprise 0.012564671101256468
disgust 0.012564671101256468
anxiety 0.012564671101256468
envy 0.012564671101256468
hope 0.012564671101256468
nervousness 0.012564671101256468
concern 0.012564671101256468
elation 0.011086474501108648
melancholy 0.009608277900960829
regret 0.009608277900960829
tiredness 0.009608277900960829
boredom 0.008130081300813009
relief 0.008130081300813009
contentment 0.008130081300813009
hatred 0.008130081300813009
thrill 0.0066518847006651885
worry 0.0066518847006651885
embarrassment 0.0066518847006651885
guilt 0.0066518847006651885
loneliness 0.0066518847006651885
joy 0.00665

features are a default dict of freqdists
dict\[(emotion label, annotation gloss)\] = {'yes': count, 'no': count} 

In [ ]:
print("observed feature frequencies:")
print(k._feature_freqdist)

observed feature frequencies:
defaultdict(<class 'nltk.probability.FreqDist'>, {('jealousy', 'e.valence==positive'): FreqDist({'no': 9}), ('jealousy', 'directed(e,otherPerson)'): FreqDist({'yes': 5, 'no': 2}), ('jealousy', 'e==anger'): FreqDist({'no': 8}), ('jealousy', 'e.duration==long'): FreqDist({'other': 3, 'yes': 3, 'no': 2}), ('jealousy', 'similar(e,anger)'): FreqDist({'yes': 3, 'other': 1}), ('jealousy', 'cause(something,e)'): FreqDist({'yes': 5}), ('jealousy', 'e==regret'): FreqDist({'no': 4}), ('jealousy', 'e==guilt'): FreqDist({'no': 1}), ('jealousy', 'e==frustration'): FreqDist({'no': 7}), ('jealousy', 'e==jealousy'): FreqDist({'yes': 10}), ('boredom', 'e.valence==positive'): FreqDist({'no': 4}), ('boredom', 'e.duration==long'): FreqDist({'yes': 2, 'no': 1}), ('boredom', 'cause(e,inactivity)'): FreqDist({'yes': 1}), ('boredom', 'e==depression'): FreqDist({'no': 4}), ('boredom', 'e==sadness'): FreqDist({'no': 3}), ('boredom', 'directed(e,otherPerson)'): FreqDist({'other': 1, 

looks like some features have value {None: 1}, this is a default value, shows that the data is mostly sparse

In [ ]:
for feature in sorted(k._feature_freqdist):
    fvals = k._feature_freqdist[feature]
    print(feature, "\t", [{v: fvals[v]} for v in fvals])
#fd  = k._feature_freqdist[('accepting', 'e==resentment')]

('accepting', 'associated(e,aggravation)') 	 [{None: 1}]
('accepting', 'associated(e,anger)') 	 [{None: 1}]
('accepting', 'associated(e,annoyance)') 	 [{None: 1}]
('accepting', 'associated(e,blame)') 	 [{None: 1}]
('accepting', 'associated(e,depression)') 	 [{None: 1}]
('accepting', 'associated(e,disappointment)') 	 [{None: 1}]
('accepting', 'associated(e,embarrassment)') 	 [{None: 1}]
('accepting', 'associated(e,fear)') 	 [{None: 1}]
('accepting', 'associated(e,goodKarma)') 	 [{None: 1}]
('accepting', 'associated(e,happiness)') 	 [{'no': 1}, {'yes': 1}]
('accepting', 'associated(e,irritation)') 	 [{None: 1}]
('accepting', 'associated(e,optimism)') 	 [{None: 1}]
('accepting', 'associated(e,otherPerson)') 	 [{None: 1}]
('accepting', 'associated(e,sadness)') 	 [{None: 1}]
('accepting', 'associated(e,satisfaction)') 	 [{None: 1}]
('accepting', 'associated(e,suffering)') 	 [{None: 1}]
('accepting', 'behavior(e,bodyMovement)') 	 [{None: 1}]
('accepting', 'behavior(e,crying)') 	 [{None: 1}]


('admiration', 'e==delight') 	 [{None: 1}]
('admiration', 'e==depression') 	 [{None: 1}]
('admiration', 'e==despair') 	 [{None: 1}]
('admiration', 'e==devastated') 	 [{None: 1}]
('admiration', 'e==disappointed') 	 [{None: 1}]
('admiration', 'e==disappointment') 	 [{None: 1}]
('admiration', 'e==disgust') 	 [{None: 1}]
('admiration', 'e==dissatisfied') 	 [{None: 1}]
('admiration', 'e==dread') 	 [{None: 1}]
('admiration', 'e==dumbfounded') 	 [{None: 1}]
('admiration', 'e==eagerness') 	 [{None: 1}]
('admiration', 'e==ecstasy') 	 [{None: 1}]
('admiration', 'e==elation') 	 [{None: 1}]
('admiration', 'e==embarrassment') 	 [{None: 1}]
('admiration', 'e==enthusiasm') 	 [{None: 1}]
('admiration', 'e==envy') 	 [{None: 1}]
('admiration', 'e==euphoria') 	 [{None: 1}]
('admiration', 'e==exasperated') 	 [{None: 1}]
('admiration', 'e==exasperation') 	 [{None: 1}]
('admiration', 'e==excited') 	 [{None: 1}]
('admiration', 'e==excitement') 	 [{None: 1}]
('admiration', 'e==exhilaration') 	 [{None: 1}]
('a

('adoration', 'mixable(e,sadness)') 	 [{None: 1}]
('adoration', 'necessary(directed(e,otherPerson))') 	 [{'yes': 1}]
('adoration', 'personalityTrait(e)') 	 [{None: 1}]
('adoration', 'similar(e,admiration)') 	 [{None: 1}]
('adoration', 'similar(e,anger)') 	 [{None: 1}]
('adoration', 'similar(e,contentment)') 	 [{None: 1}]
('adoration', 'similar(e,depression)') 	 [{None: 1}]
('adoration', 'similar(e,disappointment)') 	 [{None: 1}]
('adoration', 'similar(e,excitement)') 	 [{None: 1}]
('adoration', 'similar(e,faith)||similar(e,trust)') 	 [{None: 1}]
('adoration', 'similar(e,fury)') 	 [{None: 1}]
('adoration', 'similar(e,happiness)') 	 [{None: 1}]
('adoration', 'similar(e,happy)') 	 [{None: 1}]
('adoration', 'similar(e,hope)') 	 [{None: 1}]
('adoration', 'similar(e,informed)||similar(e,vigilant)') 	 [{None: 1}]
('adoration', 'similar(e,love)') 	 [{None: 1}]
('adoration', 'similar(e,optimism)') 	 [{None: 1}]
('adoration', 'similar(e,pain)') 	 [{None: 1}]
('adoration', 'similar(e,pride)') 	 [

('agitation', 'associated(e,sadness)') 	 [{None: 1}]
('agitation', 'associated(e,satisfaction)') 	 [{None: 1}]
('agitation', 'associated(e,suffering)') 	 [{None: 1}]
('agitation', 'behavior(e,bodyMovement)') 	 [{None: 1}]
('agitation', 'behavior(e,crying)') 	 [{None: 1}]
('agitation', 'behavior(e,laughing)') 	 [{None: 1}]
('agitation', 'behavior(e,verbal)') 	 [{None: 1}]
('agitation', 'cause(e,action)') 	 [{None: 1}]
('agitation', 'cause(e,benefit(otherPerson))') 	 [{None: 1}]
('agitation', 'cause(e,feelGood)') 	 [{None: 1}]
('agitation', 'cause(e,inactivity)') 	 [{None: 1}]
('agitation', 'cause(emptySet,e)') 	 [{'yes': 2}]
('agitation', 'cause(otherPerson,e)') 	 [{'yes': 1}]
('agitation', 'cause(something,e)') 	 [{None: 1}]
('agitation', 'directed(e,friend)') 	 [{None: 1}]
('agitation', 'directed(e,otherPerson)') 	 [{'yes': 2}]
('agitation', 'directed(e,self)') 	 [{'yes': 1}]
('agitation', 'directed(e,stranger)') 	 [{None: 1}]
('agitation', 'e.activation==high') 	 [{'no': 1}]
('agitat

('alienation', 'e==devastated') 	 [{None: 1}]
('alienation', 'e==disappointed') 	 [{None: 1}]
('alienation', 'e==disappointment') 	 [{'no': 1}]
('alienation', 'e==disgust') 	 [{'no': 1}]
('alienation', 'e==dissatisfied') 	 [{None: 1}]
('alienation', 'e==dread') 	 [{None: 1}]
('alienation', 'e==dumbfounded') 	 [{None: 1}]
('alienation', 'e==eagerness') 	 [{None: 1}]
('alienation', 'e==ecstasy') 	 [{None: 1}]
('alienation', 'e==elation') 	 [{None: 1}]
('alienation', 'e==embarrassment') 	 [{None: 1}]
('alienation', 'e==enthusiasm') 	 [{None: 1}]
('alienation', 'e==envy') 	 [{None: 1}]
('alienation', 'e==euphoria') 	 [{None: 1}]
('alienation', 'e==exasperated') 	 [{None: 1}]
('alienation', 'e==exasperation') 	 [{None: 1}]
('alienation', 'e==excited') 	 [{None: 1}]
('alienation', 'e==excitement') 	 [{None: 1}]
('alienation', 'e==exhilaration') 	 [{None: 1}]
('alienation', 'e==fear') 	 [{'no': 1}]
('alienation', 'e==focused') 	 [{None: 1}]
('alienation', 'e==frustration') 	 [{'no': 1}]
('ali

...

('thankfulness', 'similar(e,optimism)') 	 [{None: 1}]
('thankfulness', 'similar(e,pain)') 	 [{None: 1}]
('thankfulness', 'similar(e,pride)') 	 [{None: 1}]
('thankfulness', 'similar(e,rage)') 	 [{None: 1}]
('thankfulness', 'similar(e,regret)') 	 [{None: 1}]
('thankfulness', 'similar(e,sadness)') 	 [{None: 1}]
('thankfulness', 'similar(e,satisfaction)') 	 [{None: 1}]
('thankfulness', 'similar(e,scared)') 	 [{None: 1}]
('thankfulness', 'similar(e,shame)') 	 [{None: 1}]
('thankfulness', 'similar(e,stressedOut)') 	 [{None: 1}]
('thankfulness', 'similar(e,surprise)') 	 [{None: 1}]
('thankfulness', 'similarity(e,anger)>similarity(e,sadness)') 	 [{None: 1}]
('thankfulness', 'similarity(e,red)>similarity(e,blue)') 	 [{None: 1}]
('thankfulness', 'situation(e,afterGreatAccomplishment)') 	 [{None: 1}]
('thankfulness', 'situation(e,afterNastySurprise)') 	 [{None: 1}]
('thankfulness', 'situation(e,afterNastySurprise)}') 	 [{None: 1}]
('thankfulness', 'situation(e,atHauntedHouse)') 	 [{None: 1}]
('th

('tiredness', 'similar(e,excitement)') 	 [{None: 1}]
('tiredness', 'similar(e,faith)||similar(e,trust)') 	 [{None: 1}]
('tiredness', 'similar(e,fury)') 	 [{None: 1}]
('tiredness', 'similar(e,happiness)') 	 [{'no': 1}]
('tiredness', 'similar(e,happy)') 	 [{None: 1}]
('tiredness', 'similar(e,hope)') 	 [{None: 1}]
('tiredness', 'similar(e,informed)||similar(e,vigilant)') 	 [{None: 1}]
('tiredness', 'similar(e,love)') 	 [{None: 1}]
('tiredness', 'similar(e,optimism)') 	 [{None: 1}]
('tiredness', 'similar(e,pain)') 	 [{'no': 1}]
('tiredness', 'similar(e,pride)') 	 [{None: 1}]
('tiredness', 'similar(e,rage)') 	 [{None: 1}]
('tiredness', 'similar(e,regret)') 	 [{None: 1}]
('tiredness', 'similar(e,sadness)') 	 [{None: 1}]
('tiredness', 'similar(e,satisfaction)') 	 [{None: 1}]
('tiredness', 'similar(e,scared)') 	 [{None: 1}]
('tiredness', 'similar(e,shame)') 	 [{None: 1}]
('tiredness', 'similar(e,stressedOut)') 	 [{None: 1}]
('tiredness', 'similar(e,surprise)') 	 [{None: 1}]
('tiredness', 'simi

('uncomfortable', 'e==pleasure') 	 [{None: 1}]
('uncomfortable', 'e==pride') 	 [{None: 1}]
('uncomfortable', 'e==proud') 	 [{None: 1}]
('uncomfortable', 'e==regret') 	 [{None: 1}]
('uncomfortable', 'e==relaxation') 	 [{None: 1}]
('uncomfortable', 'e==relaxed') 	 [{None: 1}]
('uncomfortable', 'e==relief') 	 [{None: 1}]
('uncomfortable', 'e==remorse') 	 [{None: 1}]
('uncomfortable', 'e==resentment') 	 [{None: 1}]
('uncomfortable', 'e==sadness') 	 [{None: 1}]
('uncomfortable', 'e==sarcasm') 	 [{None: 1}]
('uncomfortable', 'e==satisfaction') 	 [{None: 1}]
('uncomfortable', 'e==scared') 	 [{None: 1}]
('uncomfortable', 'e==serenity') 	 [{None: 1}]
('uncomfortable', 'e==shame') 	 [{None: 1}]
('uncomfortable', 'e==shock') 	 [{None: 1}]
('uncomfortable', 'e==shyness') 	 [{None: 1}]
('uncomfortable', 'e==silly') 	 [{None: 1}]
('uncomfortable', 'e==sorrow') 	 [{None: 1}]
('uncomfortable', 'e==stress') 	 [{None: 1}]
('uncomfortable', 'e==surprise') 	 [{None: 1}]
('uncomfortable', 'e==suspicion') 	

('unsure', 'subset(e,humorous)') 	 [{None: 1}]
('unsure', 'unexpected(e)') 	 [{'yes': 1}]
('upset', 'associated(e,aggravation)') 	 [{None: 1}]
('upset', 'associated(e,anger)') 	 [{None: 1}]
('upset', 'associated(e,annoyance)') 	 [{None: 1}]
('upset', 'associated(e,blame)') 	 [{None: 1}]
('upset', 'associated(e,depression)') 	 [{None: 1}]
('upset', 'associated(e,disappointment)') 	 [{None: 1}]
('upset', 'associated(e,embarrassment)') 	 [{None: 1}]
('upset', 'associated(e,fear)') 	 [{None: 1}]
('upset', 'associated(e,goodKarma)') 	 [{None: 1}]
('upset', 'associated(e,happiness)') 	 [{'no': 1}]
('upset', 'associated(e,irritation)') 	 [{None: 1}]
('upset', 'associated(e,optimism)') 	 [{None: 1}]
('upset', 'associated(e,otherPerson)') 	 [{None: 1}]
('upset', 'associated(e,sadness)') 	 [{None: 1}]
('upset', 'associated(e,satisfaction)') 	 [{None: 1}]
('upset', 'associated(e,suffering)') 	 [{None: 1}]
('upset', 'behavior(e,bodyMovement)') 	 [{None: 1}]
('upset', 'behavior(e,crying)') 	 [{None

('wariness', 'e==apprehension') 	 [{None: 1}]
('wariness', 'e==awe') 	 [{None: 1}]
('wariness', 'e==boredom') 	 [{None: 1}]
('wariness', 'e==bravery') 	 [{None: 1}]
('wariness', 'e==calm') 	 [{None: 1}]
('wariness', 'e==cheerfulness') 	 [{None: 1}]
('wariness', 'e==concern') 	 [{None: 1}]
('wariness', 'e==confused') 	 [{None: 1}]
('wariness', 'e==confusion') 	 [{None: 1}]
('wariness', 'e==contempt') 	 [{None: 1}]
('wariness', 'e==contentment') 	 [{None: 1}]
('wariness', 'e==curiosity') 	 [{None: 1}]
('wariness', 'e==delight') 	 [{None: 1}]
('wariness', 'e==depression') 	 [{None: 1}]
('wariness', 'e==despair') 	 [{None: 1}]
('wariness', 'e==devastated') 	 [{None: 1}]
('wariness', 'e==disappointed') 	 [{None: 1}]
('wariness', 'e==disappointment') 	 [{None: 1}]
('wariness', 'e==disgust') 	 [{None: 1}]
('wariness', 'e==dissatisfied') 	 [{None: 1}]
('wariness', 'e==dread') 	 [{None: 1}]
('wariness', 'e==dumbfounded') 	 [{None: 1}]
('wariness', 'e==eagerness') 	 [{None: 1}]
('wariness', 'e==

a feature is a question answer pair
features is a dict

In [ ]:
features = {}
features["e.valence==positive"] = "no"     # not positive
features["directed(e,otherPerson"] = "yes" # directed at someone else

In [ ]:
features = {}
features["e.valence==positive"] = "no"     # not positive
features["directed(e,otherPerson)"] = "yes" # directed at someone else

prior = k.prob_classify(features)
for e in sorted(prior.samples(), key=prior.prob, reverse=True):
    print(e, prior.prob(e))

anger 0.2578312238205966
frustration 0.11603881106909883
jealousy 0.06789247518525621
confusion 0.03966349866086023
sadness 0.03409783163610393
envy 0.032542445812481856
concern 0.027223162077207038
hatred 0.025268252042632958
tiredness 0.025161904180500662
love 0.016455932350997002
anxiety 0.01645201427186583
resentment 0.016341837886696752
disgust 0.01590964017499112
worry 0.013399830628668992
mad 0.01302761311120594
nervousness 0.012655395593742937
obsession 0.010422090488964758
fear 0.010286738664432754
dissatisfied 0.009305437936575683
agitation 0.007444350349260549
ambivalence 0.007444350349260549
misery 0.005955480279408442
depression 0.005862425900042675
regret 0.00541948705426168
disappointment 0.005359932251467599
surprise 0.005206791329997099
guilt 0.005002603434703093
boredom 0.004913271230511963
melancholy 0.004866478171173754
hate 0.004466610209556331
discontentment 0.004466610209556331
loneliness 0.004019949188600694
annoyance 0.003890913782546845
fury 0.0035732881676450

In [ ]:
features = {}
features["cause(e,feelGood)"] = "yes"     # not positive
features["cause(otherPerson,e)"] = "yes"  # caused by someone else
features["e.duration==long"] = "no"      # long duration

prior = k.prob_classify(features)
for e in sorted(prior.samples(), key=prior.prob, reverse=True):
    print(e, prior.prob(e))

happiness 0.3373167237940271
excitement 0.06249551064247842
love 0.04638668131358046
frustration 0.04131887874069711
elation 0.03471972813471022
anger 0.03247768694926806
surprise 0.03243051529066345
sadness 0.02725774965365394
euphoria 0.026707483180546304
fear 0.026230563838036562
confusion 0.023528020897147964
nervousness 0.01981864823318319
anxiety 0.01667855072091262
jealousy 0.011537632733996016
contentment 0.011191707237562278
pity 0.008902494393515436
envy 0.007783323669759225
nostalgia 0.007630709480156098
concern 0.007412689209294499
pride 0.0071219955148123515
hatred 0.00699481702347642
joy 0.006867638532140491
relaxation 0.006867638532140482
disgust 0.006726329097322784
astounded 0.006358924566796747
hope 0.006053696187590507
hate 0.0050871396534374
distress 0.0050871396534374
inquisitiveness 0.004769193425097559
hostility 0.003815354740078049
embarrassment 0.003815354740078045
relief 0.003730569079187426
depression 0.0034620811530337845
tiredness 0.003306640774734308
regre